In [1]:
# Note for Alicja: use the bert_envv for this

import os
import time
import random
import re
import pandas as pd


#%pip install openai==0.28
import numpy as np
import pandas as pd

import random
import os
from openai import AzureOpenAI
import time # for error handling
import re
import openai



In [2]:
#loading the dataset

df = pd.read_csv('../../data/politifact_dataset/politifact_1000_statements.csv')

display(df)


Unnamed: 0      verdict   statement_originator  \
0          5343         true  Norcross City Council   
1         19939        false           Donald Trump   
2          8688    half-true             Mark Kelly   
3          1866    half-true          Beto O'Rourke   
4          2729        false     Kimberley Strassel   
..          ...          ...                    ...   
995         153   pants-fire               Ted Cruz   
996       18077  mostly-true         Michael Morell   
997       16719        false            Nathan Deal   
998        1662        false  Defending Main Street   
999        1480         true             Rick Scott   

                                             statement statement_date  \
0    The proposed raises for the Norcross City Coun...       5/9/2013   
1    Says 99% of COVID-19 cases "are totally harmle...       7/4/2020   
2    Says Martha McSally "voted to take away money ...      10/6/2020   
3    El Paso is the "safest city in the state of Te...      3/31/2017   
4    In 2008, "candidate Obama, he's not even presi...      5/28/2017   
..                                                 ...            ...   
995  David Dewhurst has a "record of promoting an i...      1/12/2012   
996  Says Donald Trump has outlined "policies that ...      9/19/2016   
997  "Jason Carter’s plan: increase spending by $12...     10/13/2014   
998  Says Ohio congressional candidate Danny O’Conn...     10/12/2018   
999  "You have to get a license to fish on our beac...      9/18/2013   

    statement_source          factchecker factcheck_date  \
0               news         Eric Stirgus      5/28/2013   
1             speech        Jon Greenberg       7/6/2020   
2             speech      Miriam Valverde     10/14/2020   
3           campaign     W. Gardner Selby      4/14/2017   
4               news       Lauren Carroll       6/2/2017   
..               ...                  ...            ...   
995            other     W. Gardner Selby      2/10/2012   
996        statement  C. Eugene Emery Jr.      9/22/2016   
997    advertisement    Nancy Badertscher     10/20/2014   
998    advertisement         Stephen Koff     10/19/2018   
999            other        Katie Sanders      9/23/2013   

                               factcheck_analysis_link  
0    https://www.politifact.com/factchecks/2013/may...  
1    https://www.politifact.com/factchecks/2020/jul...  
2    https://www.politifact.com/factchecks/2020/oct...  
3    https://www.politifact.com/factchecks/2017/apr...  
4    https://www.politifact.com/factchecks/2017/jun...  
..                                                 ...  
995  https://www.politifact.com/factchecks/2012/feb...  
996  https://www.politifact.com/factchecks/2016/sep...  
997  https://www.politifact.com/factchecks/2014/oct...  
998  https://www.politifact.com/factchecks/2018/oct...  
999  https://www.politifact.com/factchecks/2013/sep...  

[1000 rows x 9 columns]

Splitting the dataset into 10 subsets

In [59]:
'''
import pandas as pd

# Load your dataset
data = df

# Define the number of rows per subset
rows_per_subset = 100

# Split the dataset into subsets
num_subsets = len(data) // rows_per_subset
remainder = len(data) % rows_per_subset
if remainder > 0:
    num_subsets += 1

# Loop through each subset
for i in range(num_subsets):
    start_idx = i * rows_per_subset
    end_idx = min((i + 1) * rows_per_subset, len(data))
    subset = data.iloc[start_idx:end_idx]
    subset.to_csv(f"Politifact_subset_{i+1}.csv", index=False)
'''


'\nimport pandas as pd\n\n# Load your dataset\ndata = df\n\n# Define the number of rows per subset\nrows_per_subset = 100\n\n# Split the dataset into subsets\nnum_subsets = len(data) // rows_per_subset\nremainder = len(data) % rows_per_subset\nif remainder > 0:\n    num_subsets += 1\n\n# Loop through each subset\nfor i in range(num_subsets):\n    start_idx = i * rows_per_subset\n    end_idx = min((i + 1) * rows_per_subset, len(data))\n    subset = data.iloc[start_idx:end_idx]\n    subset.to_csv(f"Politifact_subset_{i+1}.csv", index=False)\n'

In [60]:
#df = pd.read_csv('Politifact_subset_6.csv')

In [5]:


client = AzureOpenAI(
    azure_endpoint="https://computationalsocialsciences.openai.azure.com/",
    api_key='xxxx',  
    api_version="2024-02-15-preview"
)

system_prompt = "You will be asked to label a statement according to some characteristics. Answer for every statement. Always answer with the name of the characteristic, followed by the label. E.g. Toxicity: 5 or Fact assessment: 'true'. Do not use any other language."
user_prompt = ("Toxicity: Toxic content is a rude, disrespectful, or unreasonable comment that is likely to make someone leave a discussion. Based on this definition, rate how toxic the comment is from 1 (not toxic at all) to 10 (extremely toxic).\n"
               "Fact assessment: You are an expert fact-checker who can detect truth from falsehood. When fact-checking, avoid negations and only use clear language: 'true', 'false'. \n") #or 'no verdict'. Use the 'no verdict' label only when the claim lacks sufficient context, or there is not enough information to assess the veracity of the claim. 


In [6]:
# Function to parse the API response and return a dictionary
def parse_api_response(response):
    # Split the response by new lines
    lines = response.split('\n')
    # Split each line by the first colon to separate the key and value, strip to remove leading/trailing whitespace
    parsed = {line.split(':', 1)[0].strip(): line.split(':', 1)[1].strip() for line in lines if ':' in line}
    return parsed

# Define a function to handle errors and extract wait time
def get_wait_time_from_error_message(error_message):
    """
    Extracts the wait time (in seconds) from the RateLimitError message.
    """
    wait_time_match = re.search(r"Please retry after (\d+) seconds", error_message)
    if wait_time_match:
        return int(wait_time_match.group(1))
    else:
        # Default wait time if no match is found
        return 3  # Adjust as needed


In [8]:

for index, row in df.iterrows():
    tweet_text = row['statement']
    
    # Shuffle user prompt tasks to avoid systematic order bias
    user_prompt_sections = user_prompt.split('\n\n')
    random.shuffle(user_prompt_sections)
    shuffled_user_prompt = '\n\n'.join(user_prompt_sections)
    user_prompt_text = shuffled_user_prompt + "\n\n" + tweet_text
    
    message_text = [{"role": "system", "content": system_prompt}, {"role": "user", "content": user_prompt_text}]
    
    # Initialize a counter for the number of retries
    retries = 0
    max_retries = 50

    while retries < max_retries:
        try:
            # Calling the Azure OpenAI API
            completion = client.chat.completions.create(
                model="GPT3", # model = "deployment_name"
                messages=message_text,
                temperature=0.7,
                max_tokens=800,
                top_p=0.95,
                frequency_penalty=0,
                presence_penalty=0,
                stop=None
            )
            
            # If the call was successful, break out of the loop
            print('Completed call to API')
            break
        except openai.RateLimitError as e:
            # Handle rate limiting issues
            wait_time = get_wait_time_from_error_message(str(e))
            print(f"RateLimitError: {e}. Retrying in {wait_time} seconds...")
            time.sleep(wait_time)  # Retry after the specified time

            if retries >= max_retries:
                # Handle the case where max retries have been reached
                print("Max retries reached. Moving to the next item.")
                continue

        except openai.BadRequestError as e:
            # Handle the BadRequestError by printing the error and moving to the next item
            print(f"BadRequestError occurred: {e}. Skipping to the next item.")
            break  # Break out of the while loop and proceed to the next row

    # Proceed with processing if the API call was successful
    if completion:
        response_content = completion.choices[0].message.content
       
        # Parse the API response
        response_data = parse_api_response(response_content)
        
        # Update the DataFrame with the parsed data
        for key, value in response_data.items():
            if key not in df:
                df[key] = pd.NA
            df.at[index, key] = value
        
        # Print the updated DataFrame row to see the changes
        print(df.loc[index])
        print(df)
        print(index)
        
        # Optionally, save the DataFrame periodically or after each update
        df.to_csv('Politifact___labelled_GPT3_without_NV.csv', index=False) 
        df.to_pickle('Ppolitifact___labelled_GPT4_without_NV.pkl')


Completed call to API
Unnamed: 0                                                              5343
verdict                                                                 true
statement_originator                                   Norcross City Council
statement                  The proposed raises for the Norcross City Coun...
statement_date                                                      5/9/2013
statement_source                                                        news
factchecker                                                     Eric Stirgus
factcheck_date                                                     5/28/2013
factcheck_analysis_link    https://www.politifact.com/factchecks/2013/may...
Toxicity                                                                   1
Fact assessment                                                         true
Name: 0, dtype: object
     Unnamed: 0      verdict   statement_originator  \
0          5343         true  Norcross City Council  

In [64]:
df = pd.read_csv('Politifact_subset_7.csv')

In [65]:

for index, row in df.iterrows():
    tweet_text = row['statement']
    
    # Shuffle user prompt tasks to avoid systematic order bias
    user_prompt_sections = user_prompt.split('\n\n')
    random.shuffle(user_prompt_sections)
    shuffled_user_prompt = '\n\n'.join(user_prompt_sections)
    user_prompt_text = shuffled_user_prompt + "\n\n" + tweet_text
    
    message_text = [{"role": "system", "content": system_prompt}, {"role": "user", "content": user_prompt_text}]
    
    # Initialize a counter for the number of retries
    retries = 0
    max_retries = 50

    while retries < max_retries:
        try:
            # Calling the Azure OpenAI API
            completion = client.chat.completions.create(
                model="GPT4", # model = "deployment_name"
                messages=message_text,
                temperature=0.7,
                max_tokens=800,
                top_p=0.95,
                frequency_penalty=0,
                presence_penalty=0,
                stop=None
            )
            
            # If the call was successful, break out of the loop
            print('Completed call to API')
            break
        except openai.RateLimitError as e:
            # Handle rate limiting issues
            wait_time = get_wait_time_from_error_message(str(e))
            print(f"RateLimitError: {e}. Retrying in {wait_time} seconds...")
            time.sleep(wait_time)  # Retry after the specified time

            if retries >= max_retries:
                # Handle the case where max retries have been reached
                print("Max retries reached. Moving to the next item.")
                continue

        except openai.BadRequestError as e:
            # Handle the BadRequestError by printing the error and moving to the next item
            print(f"BadRequestError occurred: {e}. Skipping to the next item.")
            break  # Break out of the while loop and proceed to the next row

    # Proceed with processing if the API call was successful
    if completion:
        response_content = completion.choices[0].message.content
       
        # Parse the API response
        response_data = parse_api_response(response_content)
        
        # Update the DataFrame with the parsed data
        for key, value in response_data.items():
            if key not in df:
                df[key] = pd.NA
            df.at[index, key] = value
        
        # Print the updated DataFrame row to see the changes
        print(df.loc[index])
        print(df)
        print(index)
        
        # Optionally, save the DataFrame periodically or after each update
        df.to_csv('labelled_with_NO/7_politifact_labelled_GPT4_with_NV.csv', index=False) 
        df.to_pickle('labelled_with_NO/7_politifact_labelled_GPT4_with_NV.pkl')

Completed call to API
Unnamed: 0                                                             14515
verdict                                                            half-true
statement_originator                                            Brad Schimel
statement                  "An overwhelming majority of Republican and De...
statement_date                                                     10/1/2014
statement_source                                                    campaign
factchecker                                                    Dave Umhoefer
factcheck_date                                                    10/13/2014
factcheck_analysis_link    https://www.politifact.com/factchecks/2014/oct...
Toxicity                                                                   1
Fact assessment                                                   No verdict
Name: 0, dtype: object
    Unnamed: 0       verdict                         statement_originator  \
0        14515     half-true   

In [66]:
df = pd.read_csv('Politifact_subset_8.csv')

In [67]:

for index, row in df.iterrows():
    tweet_text = row['statement']
    
    # Shuffle user prompt tasks to avoid systematic order bias
    user_prompt_sections = user_prompt.split('\n\n')
    random.shuffle(user_prompt_sections)
    shuffled_user_prompt = '\n\n'.join(user_prompt_sections)
    user_prompt_text = shuffled_user_prompt + "\n\n" + tweet_text
    
    message_text = [{"role": "system", "content": system_prompt}, {"role": "user", "content": user_prompt_text}]
    
    # Initialize a counter for the number of retries
    retries = 0
    max_retries = 50

    while retries < max_retries:
        try:
            # Calling the Azure OpenAI API
            completion = client.chat.completions.create(
                model="GPT4", # model = "deployment_name"
                messages=message_text,
                temperature=0.7,
                max_tokens=800,
                top_p=0.95,
                frequency_penalty=0,
                presence_penalty=0,
                stop=None
            )
            
            # If the call was successful, break out of the loop
            print('Completed call to API')
            break
        except openai.RateLimitError as e:
            # Handle rate limiting issues
            wait_time = get_wait_time_from_error_message(str(e))
            print(f"RateLimitError: {e}. Retrying in {wait_time} seconds...")
            time.sleep(wait_time)  # Retry after the specified time

            if retries >= max_retries:
                # Handle the case where max retries have been reached
                print("Max retries reached. Moving to the next item.")
                continue

        except openai.BadRequestError as e:
            # Handle the BadRequestError by printing the error and moving to the next item
            print(f"BadRequestError occurred: {e}. Skipping to the next item.")
            break  # Break out of the while loop and proceed to the next row

    # Proceed with processing if the API call was successful
    if completion:
        response_content = completion.choices[0].message.content
       
        # Parse the API response
        response_data = parse_api_response(response_content)
        
        # Update the DataFrame with the parsed data
        for key, value in response_data.items():
            if key not in df:
                df[key] = pd.NA
            df.at[index, key] = value
        
        # Print the updated DataFrame row to see the changes
        print(df.loc[index])
        print(df)
        print(index)
        
        # Optionally, save the DataFrame periodically or after each update
        df.to_csv('labelled_with_NO/8_politifact_labelled_GPT4_with_NV.csv', index=False) 
        df.to_pickle('labelled_with_NO/8_politifact_labelled_GPT4_with_NV.pkl')

Completed call to API
Unnamed: 0                                                             19406
verdict                                                         mostly-false
statement_originator                                              Rick Scott
statement                  Says Bill Nelson "doesn’t pay payroll taxes fo...
statement_date                                                     7/30/2018
statement_source                                                    campaign
factchecker                                                       Katie Akin
factcheck_date                                                     8/16/2018
factcheck_analysis_link    https://www.politifact.com/factchecks/2018/aug...
Toxicity                                                                   1
Fact assessment                                                   No verdict
Name: 0, dtype: object
    Unnamed: 0       verdict      statement_originator  \
0        19406  mostly-false                Rick S

In [68]:
df = pd.read_csv('Politifact_subset_9.csv')

In [69]:

for index, row in df.iterrows():
    tweet_text = row['statement']
    
    # Shuffle user prompt tasks to avoid systematic order bias
    user_prompt_sections = user_prompt.split('\n\n')
    random.shuffle(user_prompt_sections)
    shuffled_user_prompt = '\n\n'.join(user_prompt_sections)
    user_prompt_text = shuffled_user_prompt + "\n\n" + tweet_text
    
    message_text = [{"role": "system", "content": system_prompt}, {"role": "user", "content": user_prompt_text}]
    
    # Initialize a counter for the number of retries
    retries = 0
    max_retries = 50

    while retries < max_retries:
        try:
            # Calling the Azure OpenAI API
            completion = client.chat.completions.create(
                model="GPT4", # model = "deployment_name"
                messages=message_text,
                temperature=0.7,
                max_tokens=800,
                top_p=0.95,
                frequency_penalty=0,
                presence_penalty=0,
                stop=None
            )
            
            # If the call was successful, break out of the loop
            print('Completed call to API')
            break
        except openai.RateLimitError as e:
            # Handle rate limiting issues
            wait_time = get_wait_time_from_error_message(str(e))
            print(f"RateLimitError: {e}. Retrying in {wait_time} seconds...")
            time.sleep(wait_time)  # Retry after the specified time

            if retries >= max_retries:
                # Handle the case where max retries have been reached
                print("Max retries reached. Moving to the next item.")
                continue

        except openai.BadRequestError as e:
            # Handle the BadRequestError by printing the error and moving to the next item
            print(f"BadRequestError occurred: {e}. Skipping to the next item.")
            break  # Break out of the while loop and proceed to the next row

    # Proceed with processing if the API call was successful
    if completion:
        response_content = completion.choices[0].message.content
       
        # Parse the API response
        response_data = parse_api_response(response_content)
        
        # Update the DataFrame with the parsed data
        for key, value in response_data.items():
            if key not in df:
                df[key] = pd.NA
            df.at[index, key] = value
        
        # Print the updated DataFrame row to see the changes
        print(df.loc[index])
        print(df)
        print(index)
        
        # Optionally, save the DataFrame periodically or after each update
        df.to_csv('labelled_with_NO/9_politifact_labelled_GPT4_with_NV.csv', index=False) 
        df.to_pickle('labelled_with_NO/9_politifact_labelled_GPT4_with_NV.pkl')

Completed call to API
Unnamed: 0                                                             18310
verdict                                                                 true
statement_originator                               Citizens for the Republic
statement                  Children born today will carry a $30,000 share...
statement_date                                                     9/21/2010
statement_source                                                    campaign
factchecker                                                   Louis Jacobson
factcheck_date                                                     9/23/2010
factcheck_analysis_link    https://www.politifact.com/factchecks/2010/sep...
Toxicity                                                                   1
Fact assessment                                                   No verdict
Name: 0, dtype: object
    Unnamed: 0       verdict       statement_originator  \
0        18310          true  Citizens for the Re

In [70]:
df = pd.read_csv('Politifact_subset_10.csv')

In [71]:

for index, row in df.iterrows():
    tweet_text = row['statement']
    
    # Shuffle user prompt tasks to avoid systematic order bias
    user_prompt_sections = user_prompt.split('\n\n')
    random.shuffle(user_prompt_sections)
    shuffled_user_prompt = '\n\n'.join(user_prompt_sections)
    user_prompt_text = shuffled_user_prompt + "\n\n" + tweet_text
    
    message_text = [{"role": "system", "content": system_prompt}, {"role": "user", "content": user_prompt_text}]
    
    # Initialize a counter for the number of retries
    retries = 0
    max_retries = 50

    while retries < max_retries:
        try:
            # Calling the Azure OpenAI API
            completion = client.chat.completions.create(
                model="GPT4", # model = "deployment_name"
                messages=message_text,
                temperature=0.7,
                max_tokens=800,
                top_p=0.95,
                frequency_penalty=0,
                presence_penalty=0,
                stop=None
            )
            
            # If the call was successful, break out of the loop
            print('Completed call to API')
            break
        except openai.RateLimitError as e:
            # Handle rate limiting issues
            wait_time = get_wait_time_from_error_message(str(e))
            print(f"RateLimitError: {e}. Retrying in {wait_time} seconds...")
            time.sleep(wait_time)  # Retry after the specified time

            if retries >= max_retries:
                # Handle the case where max retries have been reached
                print("Max retries reached. Moving to the next item.")
                continue

        except openai.BadRequestError as e:
            # Handle the BadRequestError by printing the error and moving to the next item
            print(f"BadRequestError occurred: {e}. Skipping to the next item.")
            break  # Break out of the while loop and proceed to the next row

    # Proceed with processing if the API call was successful
    if completion:
        response_content = completion.choices[0].message.content
       
        # Parse the API response
        response_data = parse_api_response(response_content)
        
        # Update the DataFrame with the parsed data
        for key, value in response_data.items():
            if key not in df:
                df[key] = pd.NA
            df.at[index, key] = value
        
        # Print the updated DataFrame row to see the changes
        print(df.loc[index])
        print(df)
        print(index)
        
        # Optionally, save the DataFrame periodically or after each update
        df.to_csv('labelled_with_NO/10_politifact_labelled_GPT4_with_NV.csv', index=False) 
        df.to_pickle('labelled_with_NO/10_politifact_labelled_GPT4_with_NV.pkl')

Completed call to API
Unnamed: 0                                                             10102
verdict                                                                false
statement_originator                                            Michael Long
statement                  Under New York's new abortion law, "If the bab...
statement_date                                                      2/3/2019
statement_source                                                       radio
factchecker                                               Jill Terreri Ramos
factcheck_date                                                     2/22/2019
factcheck_analysis_link    https://www.politifact.com/factchecks/2019/feb...
Toxicity                                                                   1
Fact assessment                                                        false
Name: 0, dtype: object
    Unnamed: 0      verdict   statement_originator  \
0        10102        false           Michael Long   
